In [1]:
import pandas as pd
import os
import s3fs
import warnings
from datetime import date, timedelta, datetime
import numpy as np

In [2]:
# Import KPI construction functions
#exec(open('0_KPI_functions.py').read())
exec(open('../0_KPI_functions.py').read())


In [3]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

BUCKET = "projet-bdc2324-team1/0_Input/Company_10"
fs.ls(BUCKET)

['projet-bdc2324-team1/0_Input/Company_10/campaigns_information.csv',
 'projet-bdc2324-team1/0_Input/Company_10/customerplus_cleaned.csv',
 'projet-bdc2324-team1/0_Input/Company_10/products_purchased_reduced.csv',
 'projet-bdc2324-team1/0_Input/Company_10/target_information.csv']

In [4]:
dic_base=['campaigns_information','customerplus_cleaned','products_purchased_reduced','target_information']
for nom_base in dic_base:
    FILE_PATH_S3_fanta = 'projet-bdc2324-team1/0_Input/Company_10/' + nom_base + '.csv'
    with fs.open(FILE_PATH_S3_fanta, mode="rb") as file_in:
        globals()[nom_base] = pd.read_csv(file_in, sep=",")

In [5]:

def display_databases(directory_path, file_name, datetime_col = None):
    """
    This function returns the file from s3 storage 
    """
    file_path = "projet-bdc2324-team1" + "/0_Input/Company_" + directory_path + "/" + file_name + ".csv"
    print("File path : ", file_path)
    with fs.open(file_path, mode="rb") as file_in:
        df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)        
    return df 


nb_compagnie=['10','11','12','13','14']
for directory_path in nb_compagnie:
    df_customerplus_clean = display_databases(directory_path, file_name = "customerplus_cleaned")
    df_campaigns_information = display_databases(directory_path, file_name = "campaigns_information", datetime_col = ['opened_at', 'sent_at', 'campaign_sent_at'])
    df_products_purchased_reduced = display_databases(directory_path, file_name = "products_purchased_reduced", datetime_col = ['purchase_date'])
    df_customerplus_clean["Number_compagnie"]=int(directory_path)
    df_campaigns_information["Number_compagnie"]=int(directory_path)
    df_products_purchased_reduced["Number_compagnie"]=int(directory_path)

    if nb_compagnie.index(directory_path)>=1:
        customerplus_clean_spectacle=pd.concat([customerplus_clean_spectacle,df_customerplus_clean],axis=0)
        campaigns_information_spectacle=pd.concat([campaigns_information_spectacle,df_campaigns_information],axis=0)
        products_purchased_reduced_spectacle=pd.concat([products_purchased_reduced_spectacle,df_products_purchased_reduced],axis=0)
    else:
        customerplus_clean_spectacle=df_customerplus_clean
        campaigns_information_spectacle=df_campaigns_information
        products_purchased_reduced_spectacle=df_products_purchased_reduced
        

In [6]:
directory_path='10'

In [7]:
 # Import customerplus
df_customerplus_clean_0 = display_databases(directory_path, file_name = "customerplus_cleaned")
df_campaigns_information = display_databases(directory_path, file_name = "campaigns_information", datetime_col = ['opened_at', 'sent_at', 'campaign_sent_at'])
df_products_purchased_reduced = display_databases(directory_path, file_name = "products_purchased_reduced", datetime_col = ['purchase_date'])


File path :  projet-bdc2324-team1/0_Input/Company_10/customerplus_cleaned.csv


/tmp/ipykernel_1282/2987234667.py:8: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)


File path :  projet-bdc2324-team1/0_Input/Company_10/campaigns_information.csv


/tmp/ipykernel_1282/2987234667.py:8: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)


File path :  projet-bdc2324-team1/0_Input/Company_10/products_purchased_reduced.csv


/tmp/ipykernel_1282/2987234667.py:8: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)


In [9]:
 #  Creation des KPI
    # KPI sur les campagnes publicitaires
df_campaigns_kpi = campaigns_kpi_function(campaigns_information = df_campaigns_information) 

 # KPI sur le comportement d'achat
df_tickets_kpi = tickets_kpi_function(tickets_information = df_products_purchased_reduced)

  # KPI sur les données socio-démographiques
df_customerplus_clean = customerplus_kpi_function(customerplus_clean = df_customerplus_clean_0)

#creation de la colonne Number compagnie
df_tickets_kpi["Number_compagnie"]=int(directory_path)
df_campaigns_kpi["Number_compagnie"]=int(directory_path)
df_customerplus_clean["Number_compagnie"]=int(directory_path)

<string>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [11]:
df_campaigns_kpi

customer_id  nb_campaigns  nb_campaigns_opened    time_to_open  \
0               29             4                  0.0             NaT   
1               37             3                  0.0             NaT   
2               39             4                  1.0 0 days 05:16:38   
3               41             4                  1.0 0 days 01:12:29   
4               44             4                  0.0             NaT   
...            ...           ...                  ...             ...   
57138       827940             1                  0.0             NaT   
57139       827941             1                  0.0             NaT   
57140       827942             1                  0.0             NaT   
57141       827943             1                  0.0             NaT   
57142       827944             1                  0.0             NaT   

       Number_compagnie  
0                    10  
1                    10  
2                    10  
3                    10  
4                    10  
...                 ...  
57138                10  
57139                10  
57140                10  
57141                10  
57142                10  

[57143 rows x 5 columns]